In [1]:
import django
import os
import pandas as pd
import numpy as np
import html
import namedentities as ne
from old_database.modules_webpage import entry_to_dict #read_publications, read_addresses, read_seminars
import time

os.environ.setdefault("DJANGO_SETTINGS_MODULE", "nanotud.settings")
from django.core.wsgi import get_wsgi_application
application = get_wsgi_application()
#from research.models import Publication


#from home.models import Room, Country, Title_full, Gender, Status
#from internal.models import Member
from external.models import Outreach
#from teaching.models import Seminar

# needed when run inter jupyter enviornment:
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true"
django.setup()

#import gender_guesser.detector as gender
import re


## Write old papers database

In [2]:
def read_addresses(file_name):
    
    with open(file_name, 'r') as file:
            content = file.read() 
    all_entries = content.split('enditem')
    
    for entry in all_entries:
        dictio = entry_to_dict(entry)
        if dictio != {}:
            try:
                df = df.append(dictio, ignore_index=True)     # append new entry to DF
            except:
                df = pd.DataFrame(dictio, index=[0])          # first time create the DF
    df = df.fillna(np.NaN)
    #ind = df[df['vorname'].isna() & df['nachname'].isna()].index.values
    #df.drop(ind,inplace=True)
    return df

In [3]:
path_outreach = 'old_database/database.press'
df_outreach = read_addresses(path_outreach)


In [4]:
df_outreach.columns

Index(['image', 'imagedentro', 'language', 'year', 'month', 'monthname', 'day',
       'dayname', 'journal', 'url', 'title', 'quasiabstract', 'abstract',
       'imagelink', 'urlpfriend', 'hour', 'type', '', 'transcript'],
      dtype='object')

**Write to Django Database**

In [5]:
for index, row in df_outreach.iterrows():
    if type(row['year'])!= float: # or row['year']!='':
        year_raw=row['year']
        year_list=year_raw.split('-')
        year_start_raw=year_list[0]
        year_end_raw=year_list[-1]
    else:
        year_raw=None
    if type(row['month'])!=float: # or row['month']!='':
        month_raw=row['month']
        month_list=month_raw.split('-')
        month_start_raw=month_list[0]
        month_end_raw=month_list[-1]  
    else:
        month_start_raw='01'
        month_end_raw='01'
    if type(row['day'])!=float: # or row['days']!='':
        day_raw=row['day']
        day_list=day_raw.split('-')
        print('yes',day_list)
        day_start_raw=day_list[0]
        day_end_raw=day_list[-1]
    else:
        day_start_raw='01'
        day_end_raw='01'
    public_raw=True
    title_raw = html.unescape(row['title'])
    if type(row['journal'])!=float:
        source_raw=html.unescape(row['journal'])
        copyright_raw=html.unescape(row['journal'])
    else:
        source_raw=None
        copyright_raw=row['url']
    if type(row['url'])!=float:
        #copyright_raw=row['url']
        article_url_raw=row['url']
    else:
        copyright_raw=None
        article_url=None
   
        
    if type(row['imagelink'])!=float:
        image_url_raw=row['imagelink']
    else:
        image_url_raw=None
    if type(row['language'])!=float:
        language_raw=row['language']
    else:
        language_raw=None
    if type(row['abstract'])!=float:
        abstract_raw=html.unescape(row['abstract'])
    elif type(row['quasiabstract'])!=float:
        abstract_raw=html.unescape(row['quasiabstract'])
    else:
        abstract_raw=None
    if type(row['quasiabstract'])!=float:
        quasiabstract_raw=html.unescape(row['quasiabstract'])
    else:
        quasiabstract_raw=None
    if row['image']!='' and type(row['image'])!=float:
        image_raw = row['image']
        '''for ending in os.listdir('uploads/outreach/img/'):
            if row['image']+'.jpg' == ending:
                image_raw='uploads/outreach/img/' + row['image']+'.jpg'
            if row['image']+'.gif' == ending:
                image_raw='uploads/outreach/img/' + row['image']+'.gif'
            if row['image']+'.png' == ending:
                image_raw='uploads/outreach/img/' + row['image']+'.png'
                '''
    if row['imagedentro']!='' and type(row['imagedentro'])!=float:
        imagedentro_raw=row['imagedentro']
        '''for ending in os.listdir('uploads/outreach/img/'):
            if row['imagedentro']+'.jpg' == ending:
                imagedentro_raw='uploads/outreach/img/' + row['imagedentro']+'.jpg'
            if row['imagedentro']+'.gif' == ending:
                imagedentro_raw='uploads/outreach/img/' + row['imagedentro]+'.gif'
            if row['imagedentro']+'.png' == ending:
                imagedentro_raw='uploads/outreach/img/' + row['imagedentro']+'.png'
                '''
    date_raw = f"{year_start_raw}-{month_start_raw}-{day_start_raw}"
    print('date_raw',date_raw)
    print(title_raw)
    if type(row['abstract'])==float: abstract_raw=''
    new_outreach = Outreach(    date=date_raw,
                          title=title_raw,
                          source= source_raw,
                          image=image_raw,
                          image_url=image_url_raw,
                          copyright=copyright_raw,
                          quasiabstract=quasiabstract_raw,
                          abstract=abstract_raw,
                          speaker_char=speaker_char_raw,
                          copyright_imgabstr=None,
                          article=None,
                          article_url=article_url_raw,
                          public=public_raw,
                        language=language_raw
                        )
    new_outreach.save()
    time.sleep(0.25)

yes ['06']
date_raw 2020-10-06
Dem künstlichen Riechen per »e-nose«-Technologie auf der Spur
yes ['21']
date_raw 2020-09-21
Künstliche Nase soll Corona riechen
yes ['18']
date_raw 2020-09-18
Dresdner wollen mit k�nstlichen Nasen Corona erschn�ffeln
yes ['06']
date_raw 2020-08-06
Dresdner Forscherteam tüftelt am schnellsten Corona-Test der Welt
yes ['03']
date_raw 2020-08-03
Forscher entwickeln Sensor zur Corona-Schnellerkennung
yes ['03']
date_raw 2020-08-03
Forscher entwickeln Sensor zur Corona-Schnellerkennung
yes ['03']
date_raw 2020-08-03
Startschuss für neues Corona-Forschungsprojekt an der TU Dresden
yes ['03']
date_raw 2020-08-03
Startschuss für neues Corona-Forschungsprojekt an der TU Dresden
yes ['07']
date_raw 2020-07-07
<p>„Echte“ Künstliche Intelligenz: Jetzt kommt der Neurotransistor</p>
yes ['23']
date_raw 2020-06-23
Nanoelektronik lernt wie das Gehirn
yes ['28']
date_raw 2020-05-28
Ein wichtiger Schritt zum Neuromorphen Rechnen: richtungsweisende Arbeit aus Dresden
yes [

yes ['16']
date_raw 2007-03-16
Ein Molekül als Schalter für den Strom
yes ['14']
date_raw 2007-03-14
Winzige Schaltkreise aus einzelnen Molekülen
yes ['22']
date_raw 2007-03-22
Organisches Molekul schließt den Schaltkreis
yes ['08']
date_raw 2007-03-08
Wie Marmelade über dem Molekül
yes ['17']
date_raw 2007-04-17
Molekulare Elektronik: Organische Schaltelemente
yes ['03']
date_raw 2007-05-03
Ein molekularer Schalter für die Elektronik
yes ['11']
date_raw 2007-04-11
Ein molekularer Schalter für die Elektronik
yes ['08']
date_raw 2007-03-08
Ein molekularer Schalter für die Elektronik
yes ['01']
date_raw 2006-09-01
Von ultrakalten Quantengasen zu heißen Plasmen
yes ['01']
date_raw 2006-08-01
Investition in den vitalen Wissenspool
yes ['03']
date_raw 2006-05-03
Vielberth symposium on "DNA nanoelectronics"
yes ['27']
date_raw 2006-01-27
Computer mit menschlichem Bauplan
yes ['28']
date_raw 2005-07-28
DNA inside
yes ['24']
date_raw 2005-01-24
DNA für den Prozessor
yes ['20']
date_raw 2003-05

Old stuff:

In [ ]:
int('    ')